In [ ]:
import tensorflow as tf
import pandas as pd

from stable_baselines.common.policies import MlpLnLstmPolicy
from stable_baselines import PPO2

from tensortrade.strategies import StableBaselinesTradingStrategy
from tensortrade.environments import TradingEnvironment
from tensortrade.rewards import RiskAdjustedReturns
from tensortrade.actions import ManagedRiskOrders
from tensortrade.instruments import Quantity, TradingPair, BTC, USD
from tensortrade.orders.criteria import StopLossCriteria, StopDirection
from tensortrade.wallets import Wallet, Portfolio
from tensortrade.exchanges.simulated import SimulatedExchange
from tensortrade.features.stationarity import LogDifference
from tensortrade.features.scalers import MinMaxNormalizer
from tensortrade.features import FeaturePipeline

WINDOW_SIZE = 1
PRICE_COLUMN = 'close'

normalize = MinMaxNormalizer(inplace=True)
difference = LogDifference(inplace=True)
feature_pipeline = FeaturePipeline(steps=[normalize])

action_scheme = ManagedRiskOrders(pairs=[USD/BTC])
reward_scheme = RiskAdjustedReturns(return_algorithm="sortino")

csv_file = tf.keras.utils.get_file(
    'Coinbase_BTCUSD_1h.csv', 'https://www.cryptodatadownload.com/cdd/Coinbase_BTCUSD_1h.csv')
ohlcv_data = pd.read_csv(csv_file, skiprows=1, index_col="Date")
ohlcv_data.columns = map(str.lower, ohlcv_data.columns)
ohlcv_data = ohlcv_data.rename(columns={'volume btc': 'volume'})

# ohlcv_data = pd.read_csv('./data/updateOHLCdata_master.csv')

exchange = SimulatedExchange(data_frame=ohlcv_data, price_column=PRICE_COLUMN, random_periods=True)

wallets = [(exchange, USD, 10000), (exchange, BTC, 0)]

portfolio = Portfolio(base_instrument=USD, wallet_tuples=wallets)

environment = TradingEnvironment(exchange=exchange,
                                 portfolio=portfolio,
                                 action_scheme=action_scheme,
                                 reward_scheme=reward_scheme,
                                 feature_pipeline=feature_pipeline,
                                 window_size=WINDOW_SIZE,
                                 observe_wallets=[USD, BTC])

print('Observation Data:')
print(environment.observation_columns)

model = PPO2
policy = MlpLnLstmPolicy
params = { "learning_rate": 1e-5, 'nminibatches': 1 }

strategy = StableBaselinesTradingStrategy(environment=environment,
                                          model=model,
                                          policy=policy,
                                          model_kwargs=params)

strategy.run(steps=50000)

W1209 22:13:39.710019 4678901184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/module.py:31: The name tf.enable_resource_variables is deprecated. Please use tf.compat.v1.enable_resource_variables instead.

W1209 22:13:39.725437 4678901184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:46: The name tf.train.AdadeltaOptimizer is deprecated. Please use tf.compat.v1.train.AdadeltaOptimizer instead.

W1209 22:13:39.726201 4678901184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:47: The name tf.train.AdagradOptimizer is deprecated. Please use tf.compat.v1.train.AdagradOptimizer instead.

W1209 22:13:39.726911 4678901184 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:48: The name tf.train.AdamOptimizer is deprecated. Please use tf.compat.v1.train

Observation Data:
['open' 'high' 'low' 'close' 'volume' 'volume usd' 'USD' 'BTC'
 'USD_locked' 'BTC_locked']


/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:480: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
I1209 22:14:13.871910 4678901184 trading_environment.py:357] Order: OrderStatus.CANCELLED | TradeSide.BUY | TradeType.MARKET | USD/BTC | 8000.00 USD | 11622.61 | None -> OrderStatus.PENDING | TradeSide.SELL | TradeType.MARKET 

I1209 22:14:14.155516 4678901184 trading_environment.py:359] P/L: 1.00334982039076
I1209 22:14:14.156459 4678901184 trading_environment.py:360] Reward (10): 0.07819149023506287
I1209 22:14:14.159327 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked   USD  USD_locked    net_worth step
0  0.852103         0.0  0.01         0.0  9966.446213    9
I1209 22:14:14.185419 4678901184 trading_environment.py:357] Order: None
I1209 22:14:14.186739 4678901184 trading_environment.py:358] Observation: [8.32442000e-05 8.34251000e-05 8.25185000e-05 8.31862000e-05
 8.75400000e-06 7.27161312e-02 1.00000100e-10 8.52103090e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:14:14.187870 4678901184 trading_environment.py:359] P/L: 0.99702721553716
I1209 22:14:14.189249 4678901184 trading_environment.py:360] Reward (11): 0.1583734476885243
I1209 22:14:14.193495 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked   USD  USD_locked     net_worth step
0  0.852103      

I1209 22:14:14.523263 4678901184 trading_environment.py:359] P/L: 0.9944052746400001
I1209 22:14:14.523648 4678901184 trading_environment.py:360] Reward (22): 0.05009681118933133
I1209 22:14:14.526263 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked     net_worth step
0  0.852104         0.0  0.0         0.0  10053.778168   21
I1209 22:14:14.548609 4678901184 trading_environment.py:357] Order: None
I1209 22:14:14.549327 4678901184 trading_environment.py:358] Observation: [7.98421000e-05 8.01498000e-05 7.92453000e-05 7.94750000e-05
 8.15280000e-06 6.49338857e-02 1.00000000e-16 8.52103930e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:14:14.550533 4678901184 trading_environment.py:359] P/L: 0.994320064248
I1209 22:14:14.551194 4678901184 trading_environment.py:360] Reward (23): 0.011272779316217434
I1209 22:14:14.553626 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth step
0  0.852104      

...

I1209 22:17:52.460561 4678901184 trading_environment.py:359] P/L: 0.3316761411381
I1209 22:17:52.461119 4678901184 trading_environment.py:360] Reward (4009): -0.012763101864472269
I1209 22:17:52.464323 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3318.775211  4008
I1209 22:17:52.495664 4678901184 trading_environment.py:357] Order: None
I1209 22:17:52.496475 4678901184 trading_environment.py:358] Observation: [6.50314000e-05 6.55013000e-05 6.50314000e-05 6.54770000e-05
 3.65210000e-06 2.38253457e-02 1.00000000e-16 8.46134200e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:17:52.497035 4678901184 trading_environment.py:359] P/L: 0.332107669575
I1209 22:17:52.497626 4678901184 trading_environment.py:360] Reward (4010): -0.012764641011922345
I1209 22:17:52.500476 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134 

I1209 22:17:52.964363 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3319.384427  4020
I1209 22:17:52.998133 4678901184 trading_environment.py:357] Order: None
I1209 22:17:52.999076 4678901184 trading_environment.py:358] Observation: [6.4949900e-05 6.5030000e-05 6.4809200e-05 6.5030000e-05 1.2215000e-06
 7.9300068e-03 1.0000000e-16 8.4613420e-09 1.0000000e-16 1.0000000e-16]
I1209 22:17:52.999927 4678901184 trading_environment.py:359] P/L: 0.33382447584651
I1209 22:17:53.000607 4678901184 trading_environment.py:360] Reward (4022): -0.012743303534571761
I1209 22:17:53.004103 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3312.953808  4021
I1209 22:17:53.040606 4678901184 trading_environment.py:357] Order: None
I1209 22:17:53.041857 4678901184 trading_environment.py:358] Observa

I1209 22:17:53.542694 4678901184 trading_environment.py:357] Order: None
I1209 22:17:53.543513 4678901184 trading_environment.py:358] Observation: [6.44001000e-05 6.48100000e-05 6.44000000e-05 6.45500000e-05
 3.56090000e-06 2.30034288e-02 1.00000000e-16 8.46134200e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:17:53.544080 4678901184 trading_environment.py:359] P/L: 0.32819852961720003
I1209 22:17:53.544677 4678901184 trading_environment.py:360] Reward (4034): -0.012749609687363285
I1209 22:17:53.547685 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3295.032685  4033
I1209 22:17:53.579214 4678901184 trading_environment.py:357] Order: None
I1209 22:17:53.580157 4678901184 trading_environment.py:358] Observation: [6.43967000e-05 6.45860000e-05 6.43488000e-05 6.44001000e-05
 2.45210000e-06 1.57978071e-02 1.00000000e-16 8.46134200e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:17:53.58088

I1209 22:17:53.944648 4678901184 trading_environment.py:359] P/L: 0.32909966252955003
I1209 22:17:53.945035 4678901184 trading_environment.py:360] Reward (4046): -0.012622604129467212
I1209 22:17:53.947607 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3345.639971  4045
I1209 22:17:53.976230 4678901184 trading_environment.py:357] Order: None
I1209 22:17:53.976889 4678901184 trading_environment.py:358] Observation: [6.41989000e-05 6.41989000e-05 6.38107000e-05 6.40295000e-05
 3.04150000e-06 1.94758907e-02 1.00000000e-16 8.46134200e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:17:53.977350 4678901184 trading_environment.py:359] P/L: 0.327707771787
I1209 22:17:53.977840 4678901184 trading_environment.py:360] Reward (4047): -0.012726538336476686
I1209 22:17:53.980656 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846

I1209 22:17:54.367565 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3271.653998  4057
I1209 22:17:54.395478 4678901184 trading_environment.py:357] Order: None
I1209 22:17:54.396325 4678901184 trading_environment.py:358] Observation: [6.65001000e-05 6.65946000e-05 6.42000000e-05 6.44107000e-05
 6.75970000e-06 4.44389503e-02 1.00000000e-16 8.46134200e-09
 1.00000000e-16 1.00000000e-16]
I1209 22:17:54.396960 4678901184 trading_environment.py:359] P/L: 0.327200091273
I1209 22:17:54.397629 4678901184 trading_environment.py:360] Reward (4059): -0.012632367650953566
I1209 22:17:54.400569 4678901184 trading_environment.py:361] Performance:         BTC  BTC_locked  USD  USD_locked    net_worth  step
0  0.846134         0.0  0.0         0.0  3324.875838  4058
